In [1]:
from os.path import join
import pandas as pd
import numpy as np
import gzip
import json
import time
import scipy.spatial
import pickle
from time import time
from sklearn.feature_extraction import DictVectorizer

from keras.preprocessing.text import text_to_word_sequence
from keras.models import Model
from keras.layers import Input, Dense
from keras.layers.merge import Dot
from keras.callbacks import EarlyStopping, TensorBoard
from keras import metrics
from keras import backend as K
from keras.models import Sequential
from keras.layers import Conv1D, MaxPooling1D, Flatten, Dense
from keras.layers.merge import Add, Dot, Concatenate
from keras.preprocessing.sequence import pad_sequences

Using TensorFlow backend.
/home/michael/Documents/deep_learning/venv/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)


In [19]:
def initEmbeddingMap(fileName):
    print("initializing embeddings")
    with open(join("data", "glove.6B", fileName)) as glove:
        return {l[0]: np.asarray(l[1:], dtype="float32") for l in [line.split() for line in glove]}

def clean(text):
    return text_to_word_sequence(text, filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n', 
                                 lower=True, split=" ")

def initRawData(input_file):
    print("initializing raw data")
    rawInputData = []
    rawOutputData = []
    with open(input_file,"r") as f:
        for i in f:
            line = f.readline()
            if len(line) < 4:
                break
            lineObj = json.loads(line)
            user = lineObj["reviewerID"]
            item = lineObj["asin"]
            rawInputDataObj = {"user": user, "asin": item}
            rawOutputDataObj = clean(lineObj["reviewText"])
            rawInputData.append(rawInputDataObj)
            rawOutputData.append(rawOutputDataObj)
    return rawInputData, rawOutputData

def group_data(inputData):
    users = {}
    items = {}
    for datum in inputData:
        u = datum["user"]
        i = datum["asin"]
        users.setdefault(u, []).append(i)
        items.setdefault(i, []).append(u)
    return users, items

def getSetFromData(key, data):
    return set([datum.get(key) for datum in data])

def seq_2_matrix(sequence, embedding_map):
    return np.array([embedding_map.get(word) for word in sequence if word in embedding_map])

def matrix_2_avg(emb_matrix):
    return np.mean(emb_matrix, 0)

def initMatInputData(rawInputData, rawOutputData, embedding_map, save=False):
    print('initializing matrix data')
    if len(rawInputData) != len(rawOutputData):
        raise ValueError("Need same size of input and output")
    users = {}
    extra_info = {}
    items = {}
    dictVect = DictVectorizer()
    for i in range(len(rawInputData)):
        vecOutput = seq_2_matrix(rawOutputData[i], embedding_map)
        rawInput = rawInputData[i]
        user = rawInput['user']
        item = rawInput['asin']
        print(vecOutput)
        users.setdefault(user, []).append(vecOutput)
        items.setdefault(item, []).append(vecOutput)
        
    matUserInputData = []
    matItemInputData = []
    users = {k: np.vstack(v) for k, v in users.items()}
    items = {k: np.vstack(v) for k, v in items.items()}
    extra_info['user_seq_sizes'] = [m.shape[0] for m in users.values()]
    extra_info['item_seq_sizes'] = [m.shape[0] for m in items.values()]
    for i in range(len(rawInputData)):
        rawInput = rawInputData[i]
        user = rawInput['user']
        item = rawInput['asin']
        matUserInputData.append(users.get(user))
        matItemInputData.append(items.get(item))
    return matUserInputData, matItemInputData, extra_info

def toKey(user, item):
    return (user, item)

def initRatingsOutputData(rawInputData, input_file):
    ratingsData = []
    userItemDict = {}
    for i in range(len(rawInputData)):
        rawInput = rawInputData[i]
        userItem = toKey(rawInput['user'], rawInput['asin'])
        userItemDict[userItem] = i
        ratingsData.append(None)
    return ratingsData

In [3]:
fileName = "data/reviews_Amazon_Instant_Video_5.json"
rawInputData, rawOutputData = initRawData(input_file=fileName)

initializing raw data


In [6]:
users, movies = group_data(rawInputData)

In [10]:
rand_idxs = np.random.permutation(len(rawOutputData))
rawInputData = [rawInputData[i] for i in rand_idxs]
rawOutputData = [rawOutputData[i] for i in rand_idxs]

In [11]:
embedding_map = initEmbeddingMap("glove.6B.50d.txt")

initializing embeddings


In [20]:
matUserInputData, matMovieInputData, extra_info = initMatInputData(rawInputData, rawOutputData, embedding_map)

initializing matrix data
[[ 0.095387   -0.16865    -0.11514    ..., -0.42103001 -0.53816998  0.13738   ]
 [ 0.55561     0.17039999  0.13692001 ..., -0.32978001  0.24824999 -0.38275   ]
 [ 0.21705     0.46515    -0.46757001 ..., -0.043782    0.41012999  0.1796    ]
 ..., 
 [ 0.41800001  0.24968    -0.41242    ..., -0.18411    -0.11514    -0.78580999]
 [ 0.48251     0.87746    -0.23455    ..., -0.41119999  0.23625     0.26451001]
 [-0.22258     0.089765    0.45857    ..., -0.23081     0.37729001
  -0.41736999]]
[[ 0.17698     0.065221    0.28547999 ..., -0.29776001  0.11035     0.22057   ]
 [ 0.27061999 -0.36596     0.097193   ..., -0.75256002 -0.17335001 -0.22587   ]
 [ 0.11891     0.15255    -0.082073   ..., -0.57511997 -0.26671001
   0.92120999]
 ..., 
 [ 0.61183    -0.22071999 -0.10898    ..., -0.043688   -0.097922    0.16806   ]
 [ 0.26357999  0.18747     0.044394   ..., -0.42936     0.52879    -0.12598   ]
 [ 0.55024999 -0.24942    -0.0009386  ...,  0.33763     0.050139
   0.334650

[[ 0.49860999 -0.12284     0.44771999 ...,  0.26394999 -0.062214
   0.62919998]
 [ 0.48642001  0.019708    0.16084    ..., -0.050574    0.19356     0.17562   ]
 [ 0.15272     0.36181    -0.22168    ...,  0.43382001 -0.084617    0.1214    ]
 ..., 
 [ 0.19253001  0.10006     0.063798   ...,  0.081191   -0.30485001 -0.30513   ]
 [ 0.70853001  0.57088    -0.4716     ..., -0.22562    -0.093918
  -0.80374998]
 [ 0.64642    -0.55599999  0.47038001 ..., -0.35831001 -0.10995    -0.447     ]]
[[ 0.53074002  0.40116999 -0.40785    ...,  0.28762001  0.1444      0.23611   ]
 [ 0.079654    0.78386003 -0.13076    ..., -0.1175     -0.098727
   0.57669002]
 [ 0.48251     0.87746    -0.23455    ..., -0.41119999  0.23625     0.26451001]
 ..., 
 [ 0.91101998 -0.22871999  0.2077     ...,  0.16692001 -0.050063
   0.19241001]
 [ 0.4084     -0.21289    -0.33160999 ...,  1.06260002 -0.19031     0.43584001]
 [-0.31905001 -0.09507    -0.049458   ..., -0.23004     0.081364   -0.035147  ]]
[[ 0.15272     0.36181  

[[ 0.60307997 -0.32023999  0.088857   ..., -0.25187001 -0.26879001  0.36657   ]
 [ 0.75138003 -0.15736     0.47207999 ...,  0.23532    -0.26337999 -0.16202   ]
 [ 0.11891     0.15255    -0.082073   ..., -0.57511997 -0.26671001
   0.92120999]
 ..., 
 [ 0.41519001  0.13167    -0.0569     ..., -0.11806    -0.34498999
  -0.86949003]
 [-0.82643002  1.09909999 -1.10039997 ...,  0.45311999 -0.37187999
  -0.65143001]
 [-0.089298    0.54512    -1.1207     ...,  0.62721997 -0.73076999  0.25854   ]]
[[-0.53482002  0.51463997  0.01403    ..., -1.01380002  0.27698001  0.43006   ]
 [ 0.34147999  0.11925    -0.073513   ..., -0.48133999 -0.46849999  0.67534   ]
 [ 0.61849999  0.64253998 -0.46551999 ..., -0.27557001  0.30899     0.48497   ]
 ..., 
 [ 0.30045     0.25005999 -0.16692001 ..., -0.07131     0.23052    -0.51938999]
 [ 0.41800001  0.24968    -0.41242    ..., -0.18411    -0.11514    -0.78580999]
 [ 0.39118999  0.34992     0.22498    ..., -0.20466    -0.0059552
   0.17460001]]
[[-0.27279001  0.

[[  5.30740023e-01   4.01169986e-01  -4.07849997e-01   1.54440001e-01
    4.77820009e-01   2.07540005e-01  -2.69510001e-01  -3.40229988e-01
   -1.08790003e-01   1.05630003e-01  -1.02890000e-01   1.08489998e-01
   -4.96809989e-01  -2.51280010e-01   8.40250015e-01   3.89490008e-01
    3.22840005e-01  -2.27970004e-01  -4.43419993e-01  -3.16489995e-01
   -1.24059997e-01  -2.81699985e-01   1.94670007e-01   5.55129983e-02
    5.67049980e-01  -1.74189997e+00  -9.11450028e-01   2.70359993e-01
    4.19270009e-01   2.02789996e-02   4.04050016e+00  -2.49430001e-01
   -2.04160005e-01  -6.27619982e-01  -5.47830015e-02  -2.68830001e-01
    1.84440002e-01   1.82040006e-01  -2.35359997e-01  -1.61550000e-01
   -2.76549995e-01   3.55059989e-02  -3.82110000e-01  -7.51340005e-04
   -2.48219997e-01   2.81639993e-01   1.28189996e-01   2.87620008e-01
    1.44400001e-01   2.36110002e-01]
 [  6.18499994e-01   6.42539978e-01  -4.65519994e-01   3.75699997e-01
    7.48380005e-01   5.37389994e-01   2.22390005e-03 

[[ 0.41800001  0.24968    -0.41242    ..., -0.18411    -0.11514    -0.78580999]
 [ 0.66426003  0.71810001  0.17513999 ..., -0.32442999  0.42451999
  -0.70973998]
 [ 0.75068003  0.053127    0.054627   ...,  0.97435999  0.27401     0.10775   ]
 ..., 
 [-0.010419    0.18859001 -1.11029994 ..., -0.66228998  0.16455001
   0.51964998]
 [ 0.26357999  0.18747     0.044394   ..., -0.42936     0.52879    -0.12598   ]
 [-0.22492     0.69449002 -0.91219002 ...,  0.14253999  0.18313     0.86878997]]
[[ 0.52904999 -0.30145001  0.056191   ...,  0.067963   -0.10931     0.17161   ]
 [ 0.70853001  0.57088    -0.4716     ..., -0.22562    -0.093918
  -0.80374998]
 [-0.27279001  0.77515    -0.10181    ..., -0.73367     0.040383    0.26657   ]
 ..., 
 [-0.66508001  0.78362     0.74452001 ...,  0.25994     0.0064557  -0.19891   ]
 [ 1.23020005  1.00800002 -0.66763002 ...,  0.069793   -0.039322
  -0.33395001]
 [-0.24552999  0.92887002  0.94635999 ..., -0.75177002  0.42186999
   0.48225001]]
[[ 0.11891     0.1

...

[[  1.18910000e-01   1.52549997e-01  -8.20730031e-02 ...,  -5.75119972e-01
   -2.66710013e-01   9.21209991e-01]
 [  2.66000003e-01   6.68259978e-01  -2.01480001e-01 ...,  -8.62209976e-01
   -4.97379988e-01   1.36739999e-01]
 [  5.30740023e-01   4.01169986e-01  -4.07849997e-01 ...,   2.87620008e-01
    1.44400001e-01   2.36110002e-01]
 ..., 
 [  2.07819998e-01   1.27130002e-01  -3.01880002e-01 ...,  -3.53009999e-01
    5.05799986e-02   1.94949992e-02]
 [  8.87329981e-04  -3.84229988e-01  -6.88549995e-01 ...,   4.41059992e-02
    5.47839999e-01   1.01460004e+00]
 [  2.31040001e-01   8.14260006e-01  -1.34280002e+00 ...,   3.54770005e-01
   -2.20449999e-01  -5.08360028e-01]]
[[ 0.17698     0.065221    0.28547999 ..., -0.29776001  0.11035     0.22057   ]
 [ 0.60224998 -0.036286   -0.31705001 ..., -0.055718    0.10712     0.69641   ]
 [ 0.68046999 -0.039263    0.30186    ..., -0.073297   -0.064699
  -0.26043999]
 ..., 
 [-0.10274    -0.79102999  1.15789998 ...,  0.37775999  0.089557
   0.496

[[ -2.65670009e-02   1.33570004e+00  -1.02800000e+00  -3.72900009e-01
    5.20120025e-01  -1.26990005e-01  -3.54330003e-01   3.78239989e-01
   -2.97160000e-01   9.38939974e-02  -3.41220014e-02   9.29610014e-01
   -1.40230000e-01  -6.32990003e-01   2.08010003e-02  -2.15330005e-01
    9.69229996e-01   4.76539999e-01  -1.00390005e+00  -2.40130007e-01
   -3.63249987e-01  -4.75700013e-03  -5.14800012e-01  -4.62599993e-01
    1.24469995e+00  -1.83159995e+00  -1.55809999e+00  -3.74650002e-01
    5.33620000e-01   2.08829999e-01   3.22090006e+00   6.45489991e-01
    3.74379992e-01  -1.76569998e-01  -2.41640005e-02   3.37859988e-01
   -4.19000000e-01   4.00810003e-01  -1.14490002e-01   5.12319990e-02
   -1.52050003e-01   2.98550010e-01  -4.40519989e-01   1.10890001e-01
   -2.46329993e-01   6.62509978e-01  -2.69490004e-01  -4.96580005e-01
   -4.16180015e-01  -2.54900008e-01]
 [ -1.31359994e-01   4.68250006e-01   7.51339972e-01   9.50510025e-01
   -3.88689995e-01  -4.42189984e-02  -9.34059978e-01 

[[-0.23763999  0.43119001 -0.72153997 ..., -0.47773999  0.37379     1.07819998]
 [ 0.43656999  0.031303    0.25946    ...,  0.43540001  0.64441001
   0.27816999]
 [-0.25725001  0.86611003 -1.20860004 ..., -0.34531    -0.2999      0.66193002]
 ..., 
 [ 0.28701001  0.54684001 -0.32982001 ...,  0.088428   -0.21883     0.13338999]
 [ 0.58288997  0.36258     0.34064999 ..., -0.16158    -0.35168999
  -0.82555002]
 [-0.068159    0.66481    -0.062478   ...,  0.82305998 -0.54023999
  -0.0017773 ]]
[[ 0.11891     0.15255    -0.082073   ..., -0.57511997 -0.26671001
   0.92120999]
 [-0.13886     1.1401     -0.85211998 ..., -1.37109995 -0.28606001
   0.28979999]
 [ 0.75541002  0.88516003  0.43915999 ..., -0.17528    -0.21658     0.21983001]
 ..., 
 [ 0.0016675  -0.16376001 -0.092648   ..., -0.024906   -0.069572
   1.13429999]
 [-0.23763999  0.43119001 -0.72153997 ..., -0.47773999  0.37379     1.07819998]
 [ 0.82773     0.24938001 -0.45247    ..., -0.54983997 -0.12805     0.23188999]]
[[ 0.28667    

[[ 0.11891     0.15255    -0.082073   ..., -0.57511997 -0.26671001
   0.92120999]
 [ 0.42761999 -0.11469     0.010506   ..., -0.034535   -0.041267
   0.25940001]
 [ 0.17698     0.065221    0.28547999 ..., -0.29776001  0.11035     0.22057   ]
 ..., 
 [-0.0046823  -0.084424    0.081132   ...,  0.045603   -0.12214    -0.036687  ]
 [ 0.61183    -0.22071999 -0.10898    ..., -0.043688   -0.097922    0.16806   ]
 [ 0.63427001  0.080184   -0.56338    ...,  0.89538997  0.30136999
  -0.29934001]]
[[ 0.26425999 -0.69826001 -0.26249999 ..., -0.0075595   0.16116001
   0.83459002]
 [ 0.39994001 -0.96034998 -0.36842999 ...,  0.47516     0.74608999
   0.80909002]
 [ 0.26818001  0.14346001 -0.27877    ..., -0.63209999 -0.25027999 -0.38097   ]
 ..., 
 [ 0.87361997 -0.13265     1.0862     ...,  0.42844    -0.38032001 -0.17093   ]
 [ 0.27691001  0.28744999 -0.29934999 ..., -0.09482    -0.21250001
   0.022074  ]
 [ 0.33076    -0.43869999 -0.32163    ...,  0.33311999 -0.22251999
   0.74457002]]
[[ 0.097055 

KeyboardInterrupt: 

In [18]:
print(matUserInputData[0][0])
print(matMovieInputData[0][0])

[ 0.095387   -0.16865    -0.11514    -0.51113999  0.38330999  0.22657999
 -0.78504002  0.67625999 -0.66856998  0.18847001  0.19963001  0.58350998
 -0.86133999 -0.39471999  1.15709996  0.51656997  0.11706     0.0062629
 -0.25929999 -0.33371001 -0.47957     0.62110001  0.66830999 -0.058046
  0.81304997 -2.34100008 -0.75436997  0.2167      0.78012002 -0.81361997
  2.9368      0.13466001 -0.38043001 -0.59614998 -0.093113   -0.2843
  0.28314     0.59790999 -0.20750999 -0.43841001 -0.34187001 -0.21166
 -0.082453    0.44007    -0.33649999 -0.091078   -0.45859    -0.42103001
 -0.53816998  0.13738   ]
[ 0.095387   -0.16865    -0.11514    -0.51113999  0.38330999  0.22657999
 -0.78504002  0.67625999 -0.66856998  0.18847001  0.19963001  0.58350998
 -0.86133999 -0.39471999  1.15709996  0.51656997  0.11706     0.0062629
 -0.25929999 -0.33371001 -0.47957     0.62110001  0.66830999 -0.058046
  0.81304997 -2.34100008 -0.75436997  0.2167      0.78012002 -0.81361997
  2.9368      0.13466001 -0.38043001 -

In [8]:
ratingsData = initRatingsOutputData(rawInputData, input_file="data/reviews_Amazon_Instant_Video_5.json")

In [9]:
class DeepCoNN():
    def __init__(self, embedding_size, hidden_size, u_seq_len, m_seq_len, filters=2, kernel_size=8, strides=6):
        self.embedding_size = embedding_size
        self.hidden_size = hidden_size
        self.filters = filters
        self.kernel_size = kernel_size
        self.inputU, self.towerU = self.create_deepconn_tower(u_seq_len)
        self.inputM, self.towerM = self.create_deepconn_tower(m_seq_len)
        self.joined = Concatenate()([self.towerU, self.towerM])
        self.outNeuron = Dense(1)(self.joined)

    def create_deepconn_tower(self, max_seq_len):
        input_layer = Input(shape=(max_seq_len, self.embedding_size))
        tower = Conv1D(filters=self.filters, kernel_size=self.kernel_size, activation="relu")(input_layer)
        tower = MaxPooling1D()(tower)
        tower = Flatten()(tower)
        tower = Dense(self.hidden_size, activation="relu")(tower)
        return input_layer, tower

    def create_deepconn_dp(self):
        dotproduct = Dot(axes=1)([self.towerU, self.towerM])
        output = Add()([self.outNeuron, dotproduct])
        self.model = Model(inputs=[self.inputU, self.inputM], outputs=[output])
        self.model.compile(optimizer='Adam', loss='mse')
        
    def train(self, matUserInputData, matItemInputData, ratingsData, u_seq_len=200, i_seq_len=200, epochs=3500, training=None):
        
        tensorboard = TensorBoard(log_dir="tf_logs/{}".format(time()))
        self.create_deepconn_dp()
        
        self.user_input = pad_sequences(np.asarray(matUserInputData), maxlen=u_seq_len)
        self.item_input = pad_sequences(np.asarray(matItemInputData), maxlen=i_seq_len)

        self.trainingN = int(len(user_input) * training) if type(training) is float else training

        self.outputs = np.asarray(ratingsData)
        print(self.model.summary())

        self.train_inputs = [self.user_input[:self.trainingN], self.item_input[:self.trainingN]]
        self.train_outputs = self.outputs[:self.trainingN]
        self.test_inputs = [self.user_input[self.trainingN:], self.item_input[self.trainingN:]]
        self.test_outputs = self.outputs[self.trainingN:]

        early_stopping = EarlyStopping(monitor='loss', patience=4)
        early_stopping_val = EarlyStopping(monitor='val_loss', patience=6)
        batch_size = 32
        
        self.history = self.model.fit(self.train_inputs, self.train_outputs, callbacks=[early_stopping, early_stopping_val, tensorboard], validation_split=0.2, batch_size=batch_size, epochs=epochs)
        self.predicts = self.model.predict(self.test_inputs)
        

In [ ]:
# Calculates median user review length and item length. We then pad each review to these numbers
ptile = 50
u_seq_len = int(np.percentile(np.array(extra_info['user_seq_sizes']), ptile))
i_seq_len = int(np.percentile(np.array(extra_info['item_seq_sizes']), ptile))
embed_dims = matUserInputData[0].shape[1]
hidden_size = 64
deepconn = DeepCoNN(embed_dims, hidden_size, u_seq_len, i_seq_len)

deepconn.train(matUserInputData, matMovieInputData, ratingsData, 
           u_seq_len=u_seq_len, i_seq_len=i_seq_len,
           epochs=20, training=None)